In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 
%load_ext autoreload

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.

In [2]:
# read in the data 
data = pd.read_csv("../breast-cancer-data.csv")
data.head(6)
data.isnull().sum()

import pandas_profiling as pp
report = pp.ProfileReport(data)
#report.to_file("report.html")
report


In [3]:
# diagnosis is the only categorical, B for benign 357 and M for melignant 212
from sklearn.preprocessing import LabelEncoder
labelencoder=LabelEncoder()
data['diagnosis'] = labelencoder.fit_transform(data['diagnosis'])
data.head()
# M = 1, B = 0

# train test split
X = data.iloc[:,3:32]  # all rows, all the features from column 3 (skip col1 id and col2 dignosis) ignore col33 which is all NAN
y = data.iloc[:, 1]  # all rows, label only
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X,y,test_size=0.2,random_state=4)


In [4]:
print(y)

0      1
1      1
2      1
3      1
4      1
      ..
564    1
565    1
566    1
567    1
568    0
Name: diagnosis, Length: 569, dtype: int64


In [5]:
# single logistic regression 
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score
from sklearn import metrics

model_LR= LogisticRegression()
model_LR.fit(X_train,y_train)

y_prob = model_LR.predict_proba(X_test)[:,1] # This will give you positive class prediction probabilities  
log_y_pred = np.where(y_prob > 0.5, 1, 0) # This will threshold the probabilities to give class predictions.
model_LR.score(X_test, log_y_pred) # what is this 1.0
print('Accuracy Score:')
print(metrics.accuracy_score(y_test,log_y_pred)) #0.90 test error on single logistic

Accuracy Score:
0.8947368421052632


In [6]:
# single LDA
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
clf = LinearDiscriminantAnalysis()
clf.fit(X_train, y_train) 

lda_y_pred = clf.predict(X_test)
print('Accuracy Score:')
print(metrics.accuracy_score(y_test,lda_y_pred)) #0.99 test error on single lda

Accuracy Score:
0.9912280701754386


In [7]:
# single KNN
from sklearn.neighbors import KNeighborsClassifier
neigh = KNeighborsClassifier(n_neighbors=1)
neigh.fit(X_train, y_train) 

knn_y_pred = neigh.predict(X_test)
print('Accuracy Score:')
print(metrics.accuracy_score(y_test,knn_y_pred)) #0.87 test error 

Accuracy Score:
0.8771929824561403


In [8]:
#SVM
from sklearn.svm import SVC
svm_model= SVC()
svm_model.fit(X_train, y_train)

svm_y_pred=svm_model.predict(X_test)
print('Accuracy Score:')
print(metrics.accuracy_score(y_test,svm_y_pred)) #0.70 test error 


Accuracy Score:
0.7017543859649122


In [9]:
#DT
from sklearn.tree import DecisionTreeClassifier
from sklearn import metrics
classifier = DecisionTreeClassifier()
classifier.fit(X_train, y_train)
dt_y_pred=classifier.predict(X_test)
print('Accuracy Score:')
print(metrics.accuracy_score(y_test,dt_y_pred)) #0.90 test accuracy, we need average test accuracy, he got 6% test error for the average

Accuracy Score:
0.868421052631579


In [10]:
%autoreload 2
import sys
sys.path.append('/kaggle/input/utility-scripts/')
from evaluate import *
n_correct, n_total, predicted_probabilites, predictions = evaluate_bagged_model(X_train, y_train, X_test, y_test, LinearDiscriminantAnalysis(), dict(), X_train.shape[1])
print(metrics.accuracy_score(y_test, predictions))

455
0.7368421052631579


In [11]:
X_train

texture_mean  perimeter_mean  area_mean  smoothness_mean  \
342         14.96           71.49      373.9          0.10330   
138         17.57           96.85      678.1          0.11670   
434         16.94           94.89      673.7          0.08924   
47          18.66           85.98      534.6          0.11580   
64          23.84           82.69      499.0          0.11220   
..            ...             ...        ...              ...   
456         29.29           74.87      415.1          0.09357   
360         18.07           79.42      491.9          0.07436   
439         15.66           89.59      606.5          0.07966   
174         15.15           67.49      349.6          0.08792   
122         20.20          166.20     1761.0          0.14470   

     compactness_mean  concavity_mean  concave_points_mean  symmetry_mean  \
342           0.09097        0.053970             0.033410         0.1776   
138           0.13050        0.153900             0.086240         0.1957   
434           0.07074        0.033460             0.028770         0.1573   
47            0.12310        0.122600             0.073400         0.2128   
64            0.12620        0.112800             0.068730         0.1905   
..                ...             ...                  ...            ...   
456           0.08574        0.071600             0.020170         0.1799   
360           0.02650        0.001194             0.005449         0.1528   
439           0.05581        0.020870             0.026520         0.1589   
174           0.04302        0.000000             0.000000         0.1928   
122           0.28670        0.426800             0.201200         0.2655   

     fractal_dimension_mean  radius_se  ...  radius_worst  texture_worst  \
342                 0.06907     0.1601  ...         11.92          19.90   
138                 0.06216     1.2960  ...         18.55          21.43   
434                 0.05703     0.3028  ...         16.31          20.54   
47                  0.06777     0.2871  ...         15.67          27.95   
64                  0.06590     0.4255  ...         17.09          33.47   
..                      ...        ...  ...           ...            ...   
456                 0.06166     0.3135  ...         13.12          38.81   
360                 0.05185     0.3511  ...         13.72          20.98   
439                 0.05586     0.2142  ...         14.91          19.31   
174                 0.05975     0.3309  ...         11.54          19.20   
122                 0.06877     1.5090  ...         26.02          23.99   

     perimeter_worst  area_worst  smoothness_worst  compactness_worst  \
342            79.76       440.0           0.14180            0.22100   
138           121.40       971.4           0.14110            0.21640   
434           102.30       777.5           0.12180            0.15500   
47            102.80       759.4           0.17860            0.41660   
64            111.80       888.3           0.18510            0.40610   
..               ...         ...               ...                ...   
456            86.04       527.8           0.14060            0.20310   
360            86.82       585.7           0.09293            0.04327   
439            96.53       688.9           0.10340            0.10170   
174            73.20       408.3           0.10760            0.06791   
122           180.90      2073.0           0.16960            0.42440   

     concavity_worst  concave_points_worst  symmetry_worst  \
342         0.229900               0.10750          0.3301   
138         0.335500               0.16670          0.3414   
434         0.122000               0.07971          0.2525   
47          0.500600               0.20880          0.3900   
64          0.402400               0.17160          0.3383   
..               ...                   ...             ...   
456         0.292300               0.06835          0.2884   
360         0